In [ ]:
from corset import Beam
import numpy as np

positions = np.array([0, 10, 20, 30, 40, 50]) * 1e-2
diameters = np.array([1024, 1029, 1026, 1020, 1106, 1084]) * 1e-6

initial_beam = Beam.fit(zs=positions, rs=diameters / 2, wavelength=1064e-9)
initial_beam

In [ ]:
import matplotlib.pyplot as plt

initial_beam.plot(limits=(-0.1, 0.6))
plt.plot(positions, diameters / 2, 'o', label='Measured data')
plt.legend()
print(f"Fitted waist: {initial_beam.waist*1e6:.2f} µm @ z={initial_beam.focus*100:.2f} cm")

In [ ]:
desired_beam = Beam.from_gauss(focus=1.0, waist=100e-6, wavelength=initial_beam.wavelength)

In [ ]:
from corset import ThinLens

lenses = [
    ThinLens(focal_length=100e-3),  # margins are optional
    ThinLens(focal_length=150e-3, left_margin=10e-3, right_margin=10e-3),
]

In [ ]:
from corset import ShiftingRange

shifting_range = ShiftingRange(left=0., right=0.8)

With everything setup, we can perform the mode matching. For this we also need to specify the maximum number of lenses to use, we choose two as this should provide enough degrees of freedom for a perfect mode overlap. By default the function will only return solutions with greater than $99.9\text{ \%}$ mode overlap meaning only "perfect" solutions while allowing for some numerical error.

In [ ]:
from corset import mode_match

solutions = mode_match(
    setup=initial_beam,
    desired_beam=desired_beam,
    ranges=[shifting_range],
    selection=lenses,
    min_elements=1,
    max_elements=2,
)
print(f"Found {len(solutions)} solutions")

In [ ]:
solutions

The solutions themselves also have a PNG representation which in addition to a plot of the setup, also includes two analysis plots, the reachability analysis and the sensitivity analysis.

In [ ]:
solutions[1]

In [ ]:
from IPython.display import display

display(*solutions)

While in theory, all solutions which produce the same 100% mode overlap should be equivalent, in practice, they differ significantly in how easy they are to set up and adjust in the lab. There are a lot of things what play into how hard this is, but the two most important quantities (from the ones we can calculate here) are the sensitivity of the individual degrees of freedom and how strongly they are coupled.

In both regards, the third solution is significantly better than the first two. The sensitivity describes, how much mode overlap we lose per distance (squared) moved. For the third solution this is $1.57\text{ \%/cm}^2$ and $0.22\text{ \%/cm}^2$ for the two lenses respectively. This means that if everything else is correct and we displace the first lens by $1\text{ cm}$ (which we have to square to $1\text{ cm}^2$), we lose about $1.57\text{ \%}$ mode overlap. For the other two solutions, the loss in overlap is much larger for such a displacement.

The second quantity, the coupling, describes how well we can adjust the lenses independently to improve the mode overlap, where lower coupling is better. If this coupling is high, we can not get a significant improvement in mode overlap by just moving one lens at a time, so we either have to move them together, or alternate many times between them to get a significant improvement, both of which are difficult to do in practice.

Somewhat related to these quantities is how independently the two degrees of freedom change the resulting waist size and location. We can see this in the reachability plot where the third solution is also the best, the first lens mostly changes the waist location while the second lens mostly changes the waist size.